## 2 Ground Control Stations (simple)

This is a first version. The two ground control stations are working in series. 

In [1]:
import numpy as np

# Custom modules
from helpers import local2global, plot_3d_interactive, kill_processes
from simulators import Simulator, Gazebo, QGC,Color
from plan import Plan, State
from oracle import Oracle,GCS

kill_processes()

## Create Plans

In [2]:
offsets = [  # east, north, up, heading
    (5, 5, 0, 90),
    (10, 0, 0, 45),
    (-5, -10, 0, 225),
    (-15, 0, 0, 0),
    (0, -20, 0, 0),
]
n_vehicles = len(offsets)
side_lens = (5, 7, 4, 3, 2)  # must agree with n_vehicles
local_paths = [
    Plan.create_square_path(side_len=side_len, alt=5) for side_len in side_lens
]
plans = [Plan.basic(wps=path, wp_margin=0.5) for path in local_paths]

## Visualization Parameters

In [3]:
homes = np.array([offset[:3] for offset in offsets])
global_paths = [
    local2global(np.array(path), home)
    for path, home in zip(local_paths, homes)
]
colors = 2*[Color.BLUE]+3*[Color.GREEN]  # must agree with n_vehicles
waypoints = {
    f"waypoint_{i+1}": {"pos": global_paths[i], "color": colors[i]}
    for i in range(n_vehicles)
}
plot_3d_interactive(
    waypoints, title="Simulation Markers", expand=[0.2, 0.2, 0.6], ground=-0.05
)

## Choose Simulator

In [4]:
simulator = Simulator(name="NONE", offsets=offsets, plans=plans)

simulator = QGC(offsets=offsets, plans=plans, origin=(-35.3633245, 149.1652241, 0, 0))

simulator = Gazebo(
    offsets=offsets,
    plans=plans,
    world_path="simulators/gazebo/worlds/runway.world",
    models=n_vehicles * ["iris"],
    colors=colors,
    markers=waypoints,
)

Launch Simulator

In [5]:
from pymavlink import mavutil
from plan.actions import get_local_position

offsets = [  # east, north, up, heading
    (5, 5, 0, 90),
    (10, 0, 0, 45),
    (-5, -10, 0, 225),
    (-15, 0, 0, 0),
    (0, -20, 0, 0),
]
homes = np.array([offset[:3] for offset in offsets])


def get_global_pos(sysid,conns):
    pos = get_local_position(conns[sysid])
    if pos is not None:
        pos = local2global(pos, homes[sysid - 1])
    return pos

def gather_broadcasts(poss,conns):
    for sysid in list(conns.keys()):
        pos = get_global_pos(sysid,conns)
        if pos is not None:
            poss[sysid] = pos
    return poss

In [6]:
from pymavlink.dialects.v20 import common as mavlink2

def listen_for_done_and_ack(conn, command_id=3000):
    """
    Listen for a STATUSTEXT("DONE") message and respond with COMMAND_ACK.
    """
    msg = conn.recv_match(type="STATUSTEXT", blocking=False)
    if msg and msg.text.strip() == "DONE":
        print(f"🟡 Received DONE from sysid={msg.get_srcSystem()}")
        conn.mav.command_ack_send(
            command=command_id,
            result=mavlink2.MAV_RESULT_ACCEPTED
        )
        return True
    return False


sysids = list(range(1,n_vehicles+1))
simulator.launch()
# orac = Oracle(sysids)
# blue_gcs = GCS(sysids[:2])
# green_gcs = GCS(sysids[2:])

from config import GCS_BASE_PORT
conns = {}
poss = {}
for sysid in sysids:
    cs_port = GCS_BASE_PORT + 10 * (sysid - 1)
    conn = mavutil.mavlink_connection(f"udp:127.0.0.1:{cs_port}")
    conns[sysid] = conn
    conns[sysid].wait_heartbeat()
    print(f"UAV logic with sys id: {sysid} is connected to Oracle")


#while orac.sysids:
while len(conns):
    poss = gather_broadcasts(poss,conns)
    for sysid in list(conns.keys()):
        msg = conns[sysid].recv_match(type="STATUSTEXT",blocking=False)
        if msg:
            print(f"{sysid}: {msg}")
            if msg.text == "DONE":
                print(f"🟡 Received DONE from sysid={sysid}")
                conns[sysid].mav.command_ack_send(
                    command=3000,
                    result=mavlink2.MAV_RESULT_ACCEPTED
                )
                del conns[sysid]
    # orac.gather_broadcasts()
    # blue_gcs.gather_broadcasts()
    # blue_gcs.save_pos()
    # green_gcs.gather_broadcasts()
    # green_gcs.save_pos()   
    # for sysid in orac.sysids:
    #     if orac.is_plan_done(sysid):
    #         orac.remove(sysid)
kill_processes()

🚀 Vehicle 1 launched (PID 3580580)
🚀 Vehicle 2 launched (PID 3580581)
🚀 Vehicle 3 launched (PID 3580582)
🚀 Vehicle 4 launched (PID 3580583)
🚀 Vehicle 5 launched (PID 3580584)
UAV logic with sys id: 1 is connected to Oracle
UAV logic with sys id: 2 is connected to Oracle
UAV logic with sys id: 3 is connected to Oracle
UAV logic with sys id: 4 is connected to Oracle
UAV logic with sys id: 5 is connected to Oracle
1: STATUSTEXT {severity : 6, text : Barometer 1 calibration complete, id : 0, chunk_seq : 0}
2: STATUSTEXT {severity : 6, text : EKF3 IMU0 initialised, id : 0, chunk_seq : 0}
1: STATUSTEXT {severity : 6, text : EKF3 IMU0 MAG0 initial yaw alignment complete, id : 0, chunk_seq : 0}
2: STATUSTEXT {severity : 6, text : EKF3 IMU1 MAG0 initial yaw alignment complete, id : 0, chunk_seq : 0}
3: STATUSTEXT {severity : 6, text : EKF3 IMU1 MAG0 initial yaw alignment complete, id : 0, chunk_seq : 0}
1: STATUSTEXT {severity : 6, text : GPS 1: probing for u-blox at 230400 baud, id : 0, chunk_

## Execute Plan

In [7]:
blue_paths = {}
for sysid,path in blue_gcs.paths.items():
    clean_path =[x for x in path if x is not None]
    blue_paths[f"uav_{sysid}"] = {"pos": clean_path, "color": colors[sysid-1]}

NameError: name 'blue_gcs' is not defined

In [ ]:
plot_3d_interactive(
    blue_paths, title="blue_gcs", expand=[0.2, 0.2, 0.6], ground=-0.05
)

In [ ]:
green_paths = {}
for sysid,path in green_gcs.paths.items():
    clean_path =[x for x in path if x is not None]
    green_paths[f"uav_{sysid}"] = {"pos": clean_path, "color": colors[sysid-1]}

plot_3d_interactive(
    green_paths, title="green_gcs", expand=[0.2, 0.2, 0.6], ground=-0.05
)